## Name: Chenxin Xiong
###  ID: 168449

### Implementation of NN (using Back-Propagation)

In [13]:
import numpy as np
from sklearn.model_selection import train_test_split
from numpy.linalg import multi_dot
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [14]:
no_of_samples = 2000

### 1. generate 2000 sets of input data with 2 dimensions randomly

In [19]:
x = np.random.rand(no_of_samples,2)

In [20]:
x1 = x[:,0]
x2 = x[:,1]

### 2. generate corresponding 2000 scalars as y based on a nonlinear function $f(x)=x_1+(x_2)^2 + (2^{x_1}-cos(x_2))^2 $, plus noise with Gaussian distribution

In [21]:
# first para: mean; second standard deviation
noise = np.random.normal(0, 0.2, no_of_samples)

In [22]:
Y = x1+(x2)**2 + (2**x1-np.cos(x2))**2 + noise

In [23]:
Y.shape

(2000,)

### 3. split dataset into training dataset and test dataset with 8:2 ratio (80% for training and 20% for testing)

In [24]:
x_train, x_test, Y_train, Y_test = train_test_split(x, Y, test_size=0.2, shuffle=True)

In [25]:
x_train.shape

(1600, 2)

In [26]:
Y_train.shape

(1600,)

### 4. forward pass/ backward pass implementation

#### relevant parameters set up
1. the number of inputs: 2
2. the number of outputs: 1
3. the number of hidden neurons: 12 (3 hidden layers, each layer has 4 neurons)
4. the number of weights: (2x4+4)+(4x4+4)+(4x4+4)+(4x1+1)=57

In [27]:
def relu(x):
    return np.maximum(x, 0)

In [28]:
def relu_derivative(x):
    x[x<=0] = 0
    x[x>0] = 1
    return x

In [29]:
def RMSE(output, target):
    output = output.squeeze()
    rmse = np.sqrt(np.mean((output-target)**2))
    return rmse

In [30]:
def test(a, weight_matrices_list, b_vectors_list):
    for i in range(len(weight_matrices_list)-1):
        z = np.matmul(weight_matrices_list[i], a) + b_vectors_list[i]
        a = relu(z)
    output = np.matmul(weight_matrices_list[-1], a)
    return output

In [44]:
training_loss_dict = {}

In [45]:
training_loss_list_whole = []
test_loss_list_whole = []

In [145]:
training_loss_list_whole_4 = []
test_loss_list_whole_4 = []

### set the times of iterations

In [31]:
no_of_iterations = 2000

### set learning rate

In [32]:
lr = 0.01

In [121]:
class mlp(object):
    def __init__(self,layer_info):
        
        self.layer_info = layer_info
        self.no_of_weight_matrices = len(layer_info) - 1
        # define the information of weight and bias parameters
        self.weight_matrices_list = []
        self.b_vectors_list = []
        self.w_size_list = []
        self.b_size_list = []
        
        self.weight_matrices_gradient_square = None
        self.b_vectors_matrices_gradient_square = None
        self.v_weight_matrices = None
        self.v_b_vectors = None
        
    def initialize_parameters(self, w_mean=0.2, w_sd=0.01, b_mean=0.2, b_sd=0.01):
        
        initialization_mean = w_mean
        initialization_standard_deviation = w_sd
        bias_initialization_mean = b_mean
        bias_initialization_standard_deviation = b_sd
        
        for i in range(self.no_of_weight_matrices):
            w_size = (layer_info[self.no_of_weight_matrices-i], layer_info[self.no_of_weight_matrices-i-1])
            b_size = (layer_info[self.no_of_weight_matrices-i], 1)
            # initialize each layer's weight using Gaussian distribution
            w = np.random.normal(initialization_mean, initialization_standard_deviation, w_size)
            b = np.random.normal(bias_initialization_mean, bias_initialization_standard_deviation, b_size)

            self.w_size_list.insert(0, w_size)
            self.weight_matrices_list.insert(0, w)
            self.b_size_list.insert(0, b_size)
            self.b_vectors_list.insert(0, b)
    
    def forward(self, x_train):
        self.z_list = []
        a = x_train.T
        self.a_list = [a]
    
        for i in range(self.no_of_weight_matrices-1):
            # wx+b
            z = np.matmul(self.weight_matrices_list[i], a) + self.b_vectors_list[i]
            self.z_list.append(z)
            a = relu(z)
            self.a_list.append(a)
        # train
        self.output = np.matmul(self.weight_matrices_list[-1], self.a_list[-1])
        return self.output
    
    def calculate_loss(self, output, Y):
    # rmse
        output = output.squeeze()
        rmse = np.sqrt(np.mean((output-Y)**2))
        return rmse
    
    def evaluate(self, x_test, Y_test):
        a = x_test.T
        for i in range(self.no_of_weight_matrices-1):
            z = np.matmul(self.weight_matrices_list[i], a) + self.b_vectors_list[i]
            a = relu(z)
        output = np.matmul(self.weight_matrices_list[-1], a)
        rmse = self.calculate_loss(output, Y_test)
        return rmse
    
    def backward(self, Y_train):
        self.weight_matrices_gradient_list = []
        self.b_vectors_gradient_list = []
        
        c_y = (1/len(Y_train)) * (self.output-Y_train.reshape(1, len(Y_train)))
        output_layer_gradient = np.matmul(c_y, self.a_list[-1].T)
        
        self.weight_matrices_gradient_list.append(output_layer_gradient)
        output_layer_gradient_b = np.matmul(c_y, np.ones((c_y.shape[1],1)))
        
        self.b_vectors_gradient_list.append(output_layer_gradient_b)
        r_weight_matrices_list = self.weight_matrices_list[::-1]
        c_a = c_y

        for i in range(self.no_of_weight_matrices-1):
            weight = r_weight_matrices_list[i]
            c_a = np.matmul(weight.T, c_a)
            a_z = relu_derivative(self.z_list[-1-i])
            c_z = c_a * a_z
            z_b = np.ones((c_z.shape[1],1))
            z_w = self.a_list[-2-i]
            c_b = np.matmul(c_z, z_b)
            c_w = np.matmul(c_z, z_w.T)
            self.b_vectors_gradient_list.insert(0, c_b)
            self.weight_matrices_gradient_list.insert(0, c_w)
            
    def update(self, optimizer):
        
        if optimizer == 'momentum':
            self.v_weight_matrices = mlp.momentum(self.v_weight_matrices, self.weight_matrices_gradient_list)
            self.v_b_vectors = mlp.momentum(self.v_b_vectors, self.b_vectors_gradient_list)
            self.weight_matrices_list = [self.weight_matrices_list[i] - lr * self.v_weight_matrices[i] for i in range(self.no_of_weight_matrices)]
            self.b_vectors_list = [self.b_vectors_list[i] - lr * self.v_b_vectors[i] for i in range(self.no_of_weight_matrices)]
        
        elif optimizer == 'adaGrad':
            self.weight_matrices_gradient_square = mlp.adaGrad(self.weight_matrices_gradient_square, self.weight_matrices_gradient_list)
            self.b_vectors_matrices_gradient_square = mlp.adaGrad(self.b_vectors_matrices_gradient_square, self.b_vectors_gradient_list)
            self.weight_matrices_list = [self.weight_matrices_list[i] - lr * (self.weight_matrices_gradient_list[i]/(np.sqrt(self.weight_matrices_gradient_square[i])+ 1e-7)) for i in range(self.no_of_weight_matrices)]
            self.b_vectors_list = [self.b_vectors_list[i] - lr * (self.b_vectors_gradient_list[i]/(np.sqrt(self.b_vectors_matrices_gradient_square[i])+ 1e-7)) for i in range(self.no_of_weight_matrices)]
        
        else:
            # no optimizer
            self.weight_matrices_list = [self.weight_matrices_list[i] - lr * self.weight_matrices_gradient_list[i] for i in range(self.no_of_weight_matrices)]
            self.b_vectors_list = [self.b_vectors_list[i] - lr * self.b_vectors_gradient_list[i] for i in range(self.no_of_weight_matrices)]
    
    @staticmethod
    def momentum(ipt, ipt_gradient, rho=0.9):
        if ipt is None:
            return ipt_gradient
        else:
            return [rho * ipt[i] + ipt_gradient[i] for i in range(len(ipt_gradient))]
    
    @staticmethod
    def adaGrad(gradient_square_list, gradient_list):
        if gradient_square_list is None:
            return [gradient * gradient for gradient in gradient_list]
        else:
            return [gradient_square_list[i] + gradient * gradient for i, gradient in enumerate(gradient_list)]

### build NN architecture

In [122]:
layer_info = [2, 4, 4, 4, 1]

In [123]:
net = mlp(layer_info)

In [124]:
net.initialize_parameters()

### train and evaluate

In [125]:
training_loss_list = []
test_loss_list = []

In [126]:
for iteration in range(no_of_iterations):
    train_output = net.forward(x_train)
    train_rmse = net.calculate_loss(train_output, Y_train)
    test_rmse = net.evaluate(x_test, Y_test)
    
    training_loss_list.append(train_rmse)
    test_loss_list.append(test_rmse)
    
    if iteration % 100 == 0:
        print('Epoch {}, training RMSE {:.4f}, test RMSE {:4f}'.format(iteration, train_rmse, test_rmse))
    net.backward(Y_train)
    net.update('momentum')

Epoch 0, training RMSE 1.1033, test RMSE 1.137210
Epoch 100, training RMSE 0.3127, test RMSE 0.327667
Epoch 200, training RMSE 0.2550, test RMSE 0.251082
Epoch 300, training RMSE 0.2551, test RMSE 0.251256
Epoch 400, training RMSE 0.2550, test RMSE 0.251088
Epoch 500, training RMSE 0.2520, test RMSE 0.246369
Epoch 600, training RMSE 0.2446, test RMSE 0.235274
Epoch 700, training RMSE 0.2415, test RMSE 0.230188
Epoch 800, training RMSE 0.2396, test RMSE 0.227902
Epoch 900, training RMSE 0.2382, test RMSE 0.226070
Epoch 1000, training RMSE 0.2371, test RMSE 0.224006
Epoch 1100, training RMSE 0.2359, test RMSE 0.222433
Epoch 1200, training RMSE 0.2343, test RMSE 0.219937
Epoch 1300, training RMSE 0.2332, test RMSE 0.217738
Epoch 1400, training RMSE 0.2323, test RMSE 0.215858
Epoch 1500, training RMSE 0.2316, test RMSE 0.214405
Epoch 1600, training RMSE 0.2310, test RMSE 0.213372
Epoch 1700, training RMSE 0.2305, test RMSE 0.212455
Epoch 1800, training RMSE 0.2301, test RMSE 0.211788
Epoch

### (1) Plot a figure of how the error decreases during learning (lr=0.01 is chosen)

In [74]:
fig = go.Figure()
for k, v in training_loss_dict.items():
    fig.add_trace(go.Scatter(y=v,
                        mode='lines',
                        name="Learning Rate {}".format(k)))
fig.update_layout(
    title='',
    xaxis_title="Times of Iterations",
    yaxis_title="Training Error (RMSE)")
fig.show()

### (2) Show the root mean squared error (RMSE) when applying the iteratively trained NN on the training set (in one color), and on the testing test (in the other color)

In [83]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=training_loss_list,
                        mode='lines',
                        name="training"))
fig.add_trace(go.Scatter(y=test_loss_list,
                        mode='lines',
                        name="test"))
fig.update_layout(
    title='',
    xaxis_title="Times of Iterations",
    yaxis_title="RMSE")
fig.show()

### (3) compare the training error  and testing error decreasing curve in 3 independent runs with different initialized weights. 
1. Gaussian distribution initialization (mean=0, standard deviation=0.1)
2. Gaussian distribution initialization (mean=0.2, standard deviation=0.01)
3. Gaussian distribution initialization (mean=0.5, standard deviation=0.001)

In [110]:
color_list = ['blue', '#EF553B']

In [112]:
fig = make_subplots(
    rows=1, cols=3,
    subplot_titles=("Gaussian(0/0.1)", "Gaussian(0.2/0.01)", "Gaussian(0.5/0.001)"))

fig.add_trace(go.Scatter(y=training_loss_list_whole[0], legendgroup="group", name="training", mode='lines', line=dict(color=color_list[0]), showlegend=True),
              row=1, col=1)
fig.add_trace(go.Scatter(y=test_loss_list_whole[0], name="test", mode='lines', line=dict(color=color_list[1])),
              row=1, col=1)

fig.add_trace(go.Scatter(y=training_loss_list_whole[1], legendgroup="group", name="training", mode='lines', line=dict(color=color_list[0])),
              row=1, col=2)
fig.add_trace(go.Scatter(y=test_loss_list_whole[1], name="test", mode='lines', line=dict(color=color_list[1])),
              row=1, col=2)

fig.add_trace(go.Scatter(y=training_loss_list_whole[2], legendgroup="group", name="training", mode='lines', line=dict(color=color_list[0])),
              row=1, col=3)
fig.add_trace(go.Scatter(y=test_loss_list_whole[2], name="test", mode='lines', line=dict(color=color_list[1])),
              row=1, col=3)

fig.update_layout(height=500, width=1100,
                  title_text="Three different initialized weights (blue: training, orange: test)")

fig.update_layout(showlegend=True)
fig.show()

### (4) show the training error curve and the testing error curve when NN has M/2 hidden units, or has 2*M

In [416]:
training_loss_list_whole_4.append(training_loss_list)
test_loss_list_whole_4.append(test_loss_list)

In [165]:
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=("M/2 hidden neurons (2)", "M*2 hidden neurons (8)"))

fig.add_trace(go.Scatter(y=training_loss_list_whole_4[0], name="training", mode='lines', line=dict(color=color_list[0])),
              row=1, col=1)
fig.add_trace(go.Scatter(y=test_loss_list_whole_4[0], name="test", mode='lines', line=dict(color=color_list[1])),
              row=1, col=1)

fig.add_trace(go.Scatter(y=training_loss_list_whole_4[1],name="training", mode='lines', line=dict(color=color_list[0])),
              row=1, col=2)
fig.add_trace(go.Scatter(y=test_loss_list_whole_4[1], name="test", mode='lines', line=dict(color=color_list[1])),
              row=1, col=2)


fig.update_layout(height=500, width=1100,
                  title_text="Two different settings of the number of hidden neurons (blue: training, orange: test)")


fig.show()

### Bonus:  Implement two types of gradient descent optimization strategies discussed in class (e.g., choosing two from momentum, AdaGrad, RMSProp, AdaDelta or Adam).

In [166]:
def momentum(ipt, ipt_gradient, rho=0.9):
    if ipt is None:
        return ipt_gradient
    else:
        return [rho * ipt[i] + ipt_gradient[i] for i in range(len(ipt_gradient))]

In [176]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=training_loss_list,
                        mode='lines',
                        name="training"))
fig.add_trace(go.Scatter(y=test_loss_list,
                        mode='lines',
                        name="test"))
fig.update_layout(
    title='Momentum (rho=0.9)',
    xaxis_title="Times of Iterations",
    yaxis_title="RMSE")
fig.show()

### same learning rate and the number of hidden neurons, using momentum converges much faster (around 2000 iterations) and obtains much smaller training and test RMSE (0.236775) cause it has the momentum to get out of the local minimals

In [177]:
def adaGrad(gradient_square_list, gradient_list):
    if gradient_square_list is None:
        return [gradient * gradient for gradient in gradient_list]
    else:
        return [gradient_square_list[i] + gradient * gradient for i, gradient in enumerate(gradient_list)]

In [188]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=training_loss_list,
                        mode='lines',
                        name="training"))
fig.add_trace(go.Scatter(y=test_loss_list,
                        mode='lines',
                        name="test"))
fig.update_layout(
    title='AdaGrad',
    xaxis_title="Times of Iterations",
    yaxis_title="RMSE")
fig.show()

### test RMSE is 0.269036 after 2000 iterations and the loss curve converges faster as well (around 1000 iterations). The gradient of the loss curve is more smooth.